In [1]:
from droneinterface import Connection, Vehicle
from pathlib import Path
from flightdata import Flight
from flightdata import State, Origin

fl = Flight.from_log("/home/td6834/projects/montserrat/BINS/00000034.BIN")
st = State.from_flight(fl, Origin.from_initial(fl))

In [2]:
from flightplotting import plotsec
plotsec(st, nmodels=0)

In [12]:
import watch_data
from pathlib import Path
import numpy as np
import pandas as pd
import plotly.graph_objects as go
from geometry  import Point
import sweep_control

class Experiment:
    def __init__(self, flight, df, name) -> None:
        self.fl = flight
        self.name = name
        self.df_di = df
        self.df_fl = sweep_control.ControlSweep.summary_from_flight(self.fl)
        self.st = State.from_flight(self.fl, Box.from_initial(self.fl))


    @staticmethod
    def from_csv(df: pd.DataFrame, fl: Flight, name):
        return Experiment(
            fl.slice_raw_t(
                slice(
                    df.timestamp.iloc[0], 
                    df.timestamp.iloc[-1], 
                    None
                )
            ),
            df,
            name
        ) 

    def state_trace(self, *args, **kwargs):
        return plotsec(self.st, *args, **kwargs ).data

    def fl_trace(self, y, *args, **kwargs):
        return go.Scatter(x=self.fl.data.index, y=y,*args, **kwargs)



class Sweep:
    def __init__(self, fl, df, exps):
        self.fl = fl
        self.df_di = df
        self.exps = exps
        self.st = State.from_flight(self.fl, Box.from_initial(self.fl))
        self.df_fl = sweep_control.ControlSweep.summary_from_flight(self.fl)
        self.summary_di = pd.DataFrame({k: v.df_di.mean() for k, v in self.exps.items()}).T
        self.summary_fl = pd.DataFrame({k: v.df_fl.mean() for k, v in self.exps.items()}).T

    @staticmethod
    def from_folder(folder):
        exps = {}
        for csv in sorted(folder.glob("*.csv")):
            if not "summary" in csv.name:
                df = pd.read_csv(csv, index_col=0)
                if len(df) > 1:
                    exps[int(csv.stem)] = Experiment.from_csv(df, fl, csv)

        fulldf = pd.concat([e.df_di for e in exps.values()], axis=0)

        return Sweep(
            fl.slice_raw_t(
                slice(
                    fulldf.timestamp.min()-2,
                    fulldf.timestamp.max()+2,
                    None
                )
            ), 
            fulldf,
            exps
        )



run = Path("/home/td6834/projects/montserrat/DroneInterfaceOutput/flight_5/Conn_2023_05_20_21_25_56")

results = dict()
for k, p in watch_data.get_recordings_in_folder(run, False).items():
    results[k] = Sweep.from_folder(p)


TypeError: 

In [9]:
res = results[0]
fig=go.Figure()
fig.add_trace(go.Scatter(x=res.df_fl.timestamp,y=res.df_fl.servo_9, mode="lines"))
fig.add_trace(go.Scatter(x=res.df_di.timestamp,y=res.df_di.servo_9, mode="markers+lines"))
fig.show()

In [11]:
res.df_fl

timestamp    current    voltage  ground_speed   airspeed  \
time_index                                                                
0.000000    1.684614e+09  25.025375  24.399633     16.213309  20.611782   
0.040004    1.684614e+09  24.516680  24.201506     16.192199  20.611782   
0.080018    1.684614e+09  24.516680  24.201506     16.173376  20.611782   
0.120017    1.684614e+09  26.129618  24.114140     16.162753  21.295343   
0.160033    1.684614e+09  26.129618  24.114140     16.149833  21.295343   
...                  ...        ...        ...           ...        ...   
139.880007  1.684614e+09  20.583588  23.909771      9.131517  18.558924   
139.919996  1.684614e+09  21.878075  23.888275      9.171343  18.357889   
139.960024  1.684614e+09  21.878075  23.888275      9.205718  18.357889   
140.000001  1.684614e+09  21.878075  23.888275      9.242713  17.809286   
140.040002  1.684614e+09  20.056280  23.830206      9.284110  17.809286   

            wind_direction  wind_speed  servo_9  servo_10  
time_index                                                 
0.000000       -160.022377    8.927183   1861.0    1160.0  
0.040004       -160.000426    8.917786   1861.0    1160.0  
0.080018       -160.000426    8.917786   1861.0    1160.0  
0.120017       -160.000426    8.917786   1861.0    1160.0  
0.160033       -159.918023    8.911818   1861.0    1160.0  
...                    ...         ...      ...       ...  
139.880007      177.622080    8.917679   1624.0    1433.0  
139.919996      177.622080    8.917679   1624.0    1433.0  
139.960024      177.624743    8.927670   1624.0    1433.0  
140.000001      177.624743    8.927670   1624.0    1433.0  
140.040002      177.627400    8.937662   1624.0    1433.0  

[3502 rows x 9 columns]

In [6]:
from flightdata import Fields
import plotly.express as px



df=results[5][1200].fl.read_fields([Fields.TXCONTROLS, Fields.SERVOS]).loc[:,["tx_controls_7", "servo_9", "servos_9"]]
px.scatter(df)

TypeError: 'Sweep' object is not subscriptable

In [7]:
from geometry import Point
from flightplotting import titlerenderer

means = pd.DataFrame({k:exp.fl.data.mean() for k, exp in results[3].items() }).T


summary = means.loc[:, [
    "current_0", 
    "battery_0", 
    "airspeed_0", 
    "velocity_x", 
    "velocity_y",
    "velocity_z",
    "wind_x",
    "wind_y",
    "servos_8",
    "servos_9"
]]
summary["wind_z"] = 0
summary["ground_speed"] = abs(Point(summary.loc[:,["velocity_x", "velocity_y", "velocity_z"]]))
summary["wind_speed"] = abs(Point(summary.loc[:,["wind_x", "wind_y", "wind_z"]]))
summary["wind_direction"] = 0
summary.columns  = [
    "current", 
    "voltage", 
    "airspeed", 
    "velocity_x", 
    "velocity_y",
    "velocity_z",
    "wind_x",
    "wind_y",
    "servo_9",
    "servo_10",
    "wind_z",
    "ground_speed",
    "wind_speed",
    "wind_direction"

]

import watch_data

fig = watch_data.plotsummary("test", summary)


fig.update_layout(height=800)

AttributeError: 'Sweep' object has no attribute 'items'

In [8]:
#[exp.state_trace() for exp in results[0].values()]
import plotly.express as px


from flightplotting import *
#create_3d_plot([exp.state_trace() for exp in results[0].values()])
fig = go.Figure()

traces = [
#    ("airspeed_0", "y", "dash" ),
    ("current_0", "y", "solid" ),
    ("tx_controls_5", "y1", "solid" )
]


for i, res in enumerate(list(results[5].values())):
    
    color = px.colors.sequential.Viridis[i*2]

    for tr in traces:
        fig.add_trace(res.fl_trace(
            res.fl.data[tr[0]], 
            line=dict(color=color, dash=tr[2]),
            name=f"{tr[0]}_{res.name.stem}",
            yaxis=tr[1]
        ))        

fig
#create_3d_plot(results[0][1200].stat
#e_trace())
#fig

AttributeError: 'Sweep' object has no attribute 'values'